## Import files

In [ ]:
from nltk.corpus import semcor
import nltk
import numpy
from nltk.corpus import wordnet as wn
import numpy as np
nltk.download('omw-1.4')

nltk.download("semcor")
nltk.download('wordnet')

[nltk_data] Downloading package semcor to /root/nltk_data...
[nltk_data]   Package semcor is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

## Code for generating tagged Sentences

In [ ]:
from nltk.corpus import semcor
tagged_sents = [[str(c) for c in s] for s in semcor.tagged_sents(tag='both')]
tagged_sents_actual = semcor.tagged_sents(tag='both')

#Saving and Loading tagged sentences

In [ ]:
import pickle


with open('/content/drive/MyDrive/CS626_Assignment3/tagged_sents.data', 'wb') as f:
        pickle.dump(tagged_sents, f)

with open('/content/drive/MyDrive/CS626_Assignment3/tagged_sents.data', 'rb') as f:
        new_data = pickle.load(f)

print(new_data[0])

['(DT The)', '(group.n.01 (NE (NNP Fulton County Grand Jury)))', '(say.v.01 (VB said))', '(friday.n.01 (NN Friday))', '(DT an)', '(investigation.n.01 (NN investigation))', '(IN of)', '(atlanta.n.01 (NN Atlanta))', "(POS 's)", '(recent.s.02 (JJ recent))', '(primary_election.n.01 (NN primary election))', '(produce.v.04 (VB produced))', '(None ``)', '(DT no)', '(evidence.n.01 (NN evidence))', "(None '')", '(IN that)', '(DT any)', '(irregularity.n.01 (NN irregularities))', '(take_place.v.01 (VB took place))', '(None .)']


In [ ]:
print(tagged_sents[2])
tagged_sents[2][1]

['(DT The)', '(september.n.01 (NN September))', '(october.n.01 (NN October))', '(term.n.02 (NN term))', '(jury.n.01 (NN jury))', '(VBD had)', '(VBN been)', '(charge.v.05 (VB charged))', '(IN by)', '(location.n.01 (NE (NNP Fulton)))', '(person.n.01 (NE (NNP Superior Court Judge Durwood Pye)))', '(TO to)', '(investigate.v.02 (VB investigate))', '(report.n.03 (NN reports))', '(IN of)', '(possible.a.02 (JJ possible))', '(None ``)', '(irregularity.n.01 (NN irregularities))', "(None '')", '(IN in)', '(DT the)', '(hard-fought.s.01 (JJ hard-fought))', '(primary.n.01 (NN primary))', '(WDT which)', '(VBD was)', '(win.v.01 (VB won))', '(IN by)', '(person.n.01 (NE (NNP Mayor-nominate Ivan Allen Jr.)))', '(None .)']


'(september.n.01 (NN September))'

## Making the tagged dataset

In [ ]:
tagged_sents[2]
tagged_dataset=[]
for sent in tagged_sents:
    my_arr=[]
    for word in sent:
        if word[1]==word[1].lower():
            #my_arr.append([word.replace("[","").replace("]","").replace("\'",""),"None"])
        #elif word[0]=="(":
            synset=word.split(" ")[0][1:]
            if word.split(" ")[1][1:] == "NE":
                pos_tag="NN"
                chunk=word.split(" ")[3:]
                chunk=" ".join(chunk).strip(")(")
            else:
                pos_tag=word.split(" ")[1][1:]
                chunk=word.split(" ")[2:]
                chunk=" ".join(chunk).strip(")(")
            #chunk=(" ").join(word.split(" ")[1:]).strip()
            #if chunk[0]=="(":
            #    chunk=chunk[1:-2].strip()
            #    if chunk[:2]=="NE":
            #        chunk=chunk[2:].strip()
            #    else:
            #        print("found other tag ", chunk[:5])
            #else:
            #    chunk=chunk[:-1].strip()
            my_arr.append([chunk,synset,pos_tag])
                
        else:
            pos_tag=word.split(" ")[0][1:]
            chunk=word.split(" ")[1][:-1]
            my_arr.append([chunk,None,pos_tag])
    tagged_dataset.append(my_arr)

## gensim word to vector download and loading

In [ ]:
import gensim
import gensim.downloader as api
import json
info = api.info()
api.load('word2vec-google-news-300', return_path=True)

[==================================================] 100.0% 1662.8/1662.8MB downloaded


'/root/gensim-data/word2vec-google-news-300/word2vec-google-news-300.gz'

In [ ]:
w2v_model = gensim.models.KeyedVectors.load_word2vec_format('/root/gensim-data/word2vec-google-news-300/word2vec-google-news-300.gz', binary=True)

## Page rank Scoring

In [ ]:
# page rank
# scores for page_rank


for sent in tagged_dataset:
     
    sentence_word_sense_matrix_3d = [[np.zeros(300).tolist()]] #3d Matrix to store sense vectors corresponding to all words in a sentence
    
    
    
    for tuple_ in sent:               
        
        chunk,sense,pos_tag=tuple_
        
        #if pos_tag!="NN":

        #Do not enter here
        if False:
            pass

        else:
            word_sense_matrix_2d = []
            if len(chunk.split(" "))<=1 or len(wn.synsets(chunk)) >0:
                
                synids=wn.synsets(chunk)
                
                for id in synids:
                    
                    words=id.definition().split(" ")
                    
                    word_vec=np.array([])
                    for word in words:
                        if len(word_vec)==0:
                            try:
                                word_vec=np.expand_dims(w2v_model.wv[word],0)
                            except:
                                word_vec = np.expand_dims(np.random.rand(300),0)
                        else:
                            try:
                                word_vec=np.append(word_vec,np.expand_dims(w2v_model.wv[word],axis=0),axis=0)
                            except:
                                word_vec=np.append(word_vec,np.expand_dims(np.random.rand(300),0),axis=0)
                    word_vec=np.mean(word_vec,axis=0)
                    word_sense_matrix_2d.append(word_vec)


            else:

                for word_chunk in chunk:
                    synids=wn.synsets(word_chunk)


                    for id in synids:
                        
                        words=id.definition().split(" ")
                        
                        word_vec=np.array([])
                        for word in words:
                            if len(word_vec)==0:
                                try:
                                    word_vec=np.expand_dims(w2v_model.wv[word],0)
                                except:
                                    word_vec = np.expand_dims(np.random.rand(300),0)
                            else:
                                try:
                                    word_vec=np.append(word_vec,np.expand_dims(w2v_model.wv[word],axis=0),axis=0)
                                except:
                                    word_vec=np.append(word_vec,np.expand_dims(np.random.rand(300),0),axis=0)
                        word_vec=np.mean(word_vec,axis=0)
                        word_sense_matrix_2d.append(word_vec)


        sentence_word_sense_matrix_3d.append(word_sense_matrix_2d)
        

        
        #break
    sentence_word_sense_matrix_3d.append([np.zeros(300).tolist()])

    for i in range(len(sentence_word_sense_matrix_3d)): 
      if len(sentence_word_sense_matrix_3d[i]) == 0:
        sentence_word_sense_matrix_3d[i] = [np.random.randn(300).tolist()]

        

    #print(sentence_word_sense_matrix_3d[3])

    

    #dict

    edge_weight = dict()

    for i in range(len(sentence_word_sense_matrix_3d) - 1):

      j = 0

      for vector1 in sentence_word_sense_matrix_3d[i] :

        k = 0

        for vector2 in sentence_word_sense_matrix_3d[i + 1]:

          vec1 = np.array(vector1)
          vec2 = np.array(vector2)

          key = str(i) + " " + str(j) + " " + str(i + 1) + " " + str(k)

          #print("vec1")
          #print(vec1)
          #print("vec2")
          #print(vec2)

          edge_weight[key] = np.dot(vec1, vec2)

          k+=1

        
        j+=1
      


    #print(sentence_word_sense_matrix_3d[7])
    print(edge_weight)

    node_sense_selected = []

    for word_no in range(1, len(sentence_word_sense_matrix_3d) - 1):

      no_prev_word_senses = len(sentence_word_sense_matrix_3d[word_no - 1])
      no_next_word_senses = len(sentence_word_sense_matrix_3d[word_no + 1])

      

      list_of_word_sense_weightage = []

      for sense in range(len(sentence_word_sense_matrix_3d[word_no])):
        sense_weight = 1

        edge_sum = 0.0
        edge_count = 0

        for i in range (no_prev_word_senses):

            key1 = str(word_no - 1) + " " + str(i) + " " + str(word_no) + " " + str(sense)

            sense_weight *= edge_weight[key1]
            edge_sum += edge_weight[key1]
            edge_count += 1

        for j in range (no_next_word_senses):

            key1 = str(word_no) + " " + str(sense) + " " + str(word_no + 1) + " " + str(j)

            sense_weight *= edge_weight[key1]
            edge_sum += edge_weight[key1]
            edge_count += 1

        sense_weight /= (edge_sum ** edge_count)

        list_of_word_sense_weightage.append(sense_weight)

      maxpos = list_of_word_sense_weightage.index(max(list_of_word_sense_weightage))
      '''print(list_of_word_sense_weightage)
      print(len(list_of_word_sense_weightage))
      print(maxpos)
      print('\n\n')'''

      node_sense_selected.append(maxpos)

      
    print(node_sense_selected)
        

    #break



    # predict_dataset.append(my_arr)
    #predict_senses.append(my_arr_senses)
    #predict_scores.append(my_arr_scores)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:61: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:66: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:35: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:40: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:159: RuntimeWarning: overflow encountered in double_scalars


{'0 0 1 0': 0.0, '1 0 2 0': -4.576574333756577, '1 0 2 1': -3.5280298002149495, '1 0 2 2': -3.7713454849495798, '1 0 2 3': -3.5651527574652513, '1 0 2 4': -2.926598745447188, '1 0 2 5': -4.106268113864032, '1 0 2 6': -6.307302014311718, '1 0 2 7': -2.598642388261762, '1 0 2 8': -3.9059804964295806, '1 0 2 9': -3.8660642789539508, '1 0 2 10': -4.183027577889321, '1 0 2 11': -2.8218404594405904, '1 0 2 12': -6.316339876957808, '1 0 2 13': -3.864043385779828, '1 0 2 14': -3.1162756271097187, '1 0 2 15': -2.984636476067033, '1 0 2 16': -7.820178550048887, '1 0 2 17': -4.448197198727132, '1 0 2 18': -4.958502875194558, '1 0 2 19': -3.556751588504573, '1 0 2 20': -5.798566447538054, '1 0 2 21': -4.256836701216849, '1 0 2 22': -4.302446205736403, '1 0 2 23': -2.7413474764448265, '1 0 2 24': -3.7258957603068694, '1 0 2 25': -4.523661035359431, '1 0 2 26': -2.1328182430768288, '1 0 2 27': -5.664664625318747, '1 0 2 28': -4.362590750928817, '1 0 2 29': -4.586842195329193, '1 0 2 30': -3.18353011

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:155: RuntimeWarning: overflow encountered in double_scalars
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:159: RuntimeWarning: invalid value encountered in double_scalars


{'0 0 1 0': 0.0, '1 0 2 0': 1.8825759982687047, '2 0 3 0': 74.0603001761597, '2 0 3 1': 73.6593554459426, '2 0 3 2': 74.31980772516796, '2 0 3 3': 74.35831657207605, '2 0 3 4': 75.71581210447235, '2 0 3 5': 75.56077910289447, '2 0 3 6': 73.47330341203313, '2 0 3 7': 75.71426353380454, '2 0 3 8': 74.69845493465998, '2 0 3 9': 75.69331357767865, '2 0 3 10': 75.1832551752203, '2 0 3 11': 76.03550804391166, '3 0 4 0': 3.5903225042357625, '3 1 4 0': 3.8601368872506066, '3 2 4 0': 5.8716129797339445, '3 3 4 0': 6.98024782981397, '3 4 4 0': 6.085544947139869, '3 5 4 0': 4.0959216796848406, '3 6 4 0': 3.173220425712793, '3 7 4 0': 1.9529677008154969, '3 8 4 0': 5.981084891537169, '3 9 4 0': 5.123699266082792, '3 10 4 0': 13.160194516992165, '3 11 4 0': 7.036809881819845, '4 0 5 0': 8.42718516603667, '4 0 5 1': 6.484310178432162, '4 0 5 2': 3.613543613717604, '4 0 5 3': 4.5172599663096085, '4 0 5 4': 8.79584864617457, '4 0 5 5': 3.5830688027983895, '5 0 6 0': 5.987690124646299, '5 1 6 0': 7.050

KeyboardInterrupt: ignored